# Lesson 1: Writing like your favorite author

In this lesson, aimed to be of introductory nature, we shall start by something easy: word prediction. The idea is to use an entire book to teach the machine which words show up sequentially. The main tool is a classical mathematical object: Markov chains.

## I. Loading books from the Project Gutenberg (https://www.gutenberg.org)

In [1]:
from __future__ import print_function
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets

#List of books along with their identifier on Project Gutenberg
# Feel free to expand the list and pick your favorite
books = { "Alice's Adventures in Wonderland": 11  , # by Lewis Carroll, 160 kb
          "The Complete Poetical Works of Edgar Allan Poe": 10031, #by Edgar Allan Poe, 400 kb
          "The Hound of the Baskervilles":    2852, # by Sir Conan Doyle, 340 kb
          "The King James Bible":             10,   # by King James, 4.3 Mb
          "The Complete Works of William Shakespeare": 100 #by William Shakespeare, 5.5 Mb
        }

def bookSelection(bookTitle):
    bookId = books[bookTitle]
    #
    print( "Loading text from Project Gutenberg URL..." )
    import urllib3
    http = urllib3.PoolManager()
    url = 'https://www.gutenberg.org/cache/epub/%s/pg%s.txt' % (bookId, bookId)
    request = http.request('GET', url)
    #
    global book
    book = request.data
    print( "Request done with %d bytes..." % len(book))
    #Converts from bytes to string
    book = book.decode("utf-8") 
    return

interact(bookSelection, bookTitle=books.keys() );


interactive(children=(Dropdown(description='bookTitle', options=("Alice's Adventures in Wonderland", 'The Comp…

In [4]:
import re #Rational expressions
words = re.split('[^A-Za-z]+', book.lower())
words = [w for w in words if w!=''] # Remove empty strings

# Computes a dictionary where keys are words
#  and values are the number of occurrences.
# Output is sorted
def generate1gram():
    gram = dict()
    
    # Populate 1-gram dictionary
    for i in range(len(words)-1):
        key = words[i]
        if gram.get(key) is None:
            gram[key] = 1
        else:
            gram[key] += 1
    
    #Warning! sorted forms a list
    gram = sorted(gram.items(), key=lambda x:-x[1])
    
    return dict(gram)

gram1 = generate1gram()

# Print length of list
print( "Total number of words, with repetition:    ", len(words) )
print( "Total number of words, without repetition: ", len(gram1) )

Total number of words, with repetition:     30419
Total number of words, without repetition:  3007


## II. Autocompletion using 1-grams

Exercice 1:
Write a function findLastWord, whose input and output are string objects. Given a string of characters, this function should isolate the last word as follows:
- transform to lower case
- strip spaces at the end
- find the last space and isolate that part

In [5]:
from IPython.display import display

# Information labels
infoLabel1 = widgets.Label(value="Input:")
infoLabel2 = widgets.Label(value="Last word:")
infoLabel3 = widgets.Label(value="Autocomplete suggestion:")
#Input area
inputArea = widgets.Textarea(
    value='',
    placeholder='Type something',
    description='',
    disabled=False
)
# Output labels
outputLastWord = widgets.Label(value='')
outputLabel = widgets.Label(value='')
output = widgets.Output()

def findLastWord(str):
    #TODO
    return ""

def onChange(change):
    with output:
        lastWord = findLastWord(change.new)
        outputLastWord.value = lastWord
        #
        #Either the last word exists in the dictionary and then nothing to do
        possibleWords = [ (w,x) for (w,x) in gram1.items() if w.startswith(lastWord)]
        outputLabel.value = ''.join( [ (w+'(%d) ')%x for (w,x) in possibleWords ] )

# Sets a callback upon the change of the TextArea's content
inputArea.observe(onChange, 'value')

display( infoLabel1, output)
display( inputArea, output)
display( widgets.HBox([infoLabel2, outputLastWord]), output)
display( infoLabel3, output)
display( outputLabel, output)

Label(value='Input:')

Output()

Textarea(value='', placeholder='Type something')

Output()

Output()

Label(value='Autocomplete suggestion:')

Output()

Label(value='')

Output()

## III. Predicting the next word: 2-grams

Exercice 2:
 - Adapt the previous function generate1gram and write a function generate2gram which returns a dictionary whose keys are pairs of words and values are the number of occurences
 - Write the function predictNextWord

In [6]:
# Computes a dictionary where keys are all pairs of words
#  and values are the number of occurrences.
# Output is sorted
def generate2gram():
    # TODO    
    return None

In [7]:
#Test
gram2 = generate2gram()
print( [(w,x) for (w,x) in gram2.items() if x>50] )

AttributeError: 'NoneType' object has no attribute 'items'

In [9]:
from IPython.display import display

# Information labels
infoLabel1 = widgets.Label(value="Input:")
infoLabel2 = widgets.Label(value="Autocomplete suggestions:")
infoLabel3 = widgets.Label(value="Suggestion from word prediction:")
#Input area
inputArea = widgets.Textarea(
    value='',
    placeholder='Type something',
    description='',
    disabled=False
)
# Output labels
outputAutocomplete = widgets.Label(value='')
outputPrediction = widgets.Label(value='')
output = widgets.Output()

def onChange(change):
    with output:
        lastWord = findLastWord( change.new )
        #
        # Autocomplete as before
        possibleWords = [ (w,x) for (w,x) in gram1.items() if w.startswith(lastWord)]
        outputAutocomplete.value = ''.join( [ w+'(%d) '%x for (w,x) in possibleWords ] )
        #
        # Prediction
        # Either the last word does not exist in the dictionary (or equivalently the 1-gram) and then nothing to do
        if lastWord not in [w for (w,x) in possibleWords]:
            outputPrediction.value = ''
        # or the last word allows to predict the next
        else:
            possiblePairs = predictNextWord(lastWord)
            outputPrediction.value = ''.join( [ (p[1]+'(%d) ') % x for (p,x) in possiblePairs ] )
        
def predictNextWord(str):
    return ""

# Sets a callback upon the change of the TextArea's content
inputArea.observe(onChange, 'value')

display( widgets.HBox( [infoLabel1, inputArea] ) , output)
display( infoLabel2, output)
display( outputAutocomplete, output)
display( infoLabel3, output )
display( outputPrediction, output)


Output()

Label(value='Autocomplete suggestions:')

Output()

Label(value='')

Output()

Label(value='Suggestion from word prediction:')

Output()

Label(value='')

Output()

# III. N-Grams (tri-grams and more...)

In this section, we generalize the Markov chain approach by predicting the next word from multiple previous words. To that end, we have to build Ngrams i.e a dictionary of N-tuples of words, counting occurrences.

Exercice 3:
1. Write a function generateNgram
2. Understand the next lines of code
3. Fill in the function generate which takes as input a string and samples a new word using word prediction
4. Write a loop that starts from the empty string and generates the next word

In [10]:
def generateNgram(n=1):
    return dict()

In [11]:
# Test
gram5 = generateNgram(5)
print( [(w,x) for (w,x) in gram5.items() if x>10] )

[]


In [12]:
maxLag = 5
Ngrams = []
for i in range(1,maxLag):
    Ngrams.append( generateNgram(i))
Ngrams.reverse() #Reverse order so that we start by Ngrams for N being the largest
print( "Generated Ngrams for N from 1 to ", len(Ngrams) )

Generated Ngrams for N from 1 to  4


In [13]:
def findLastWords(str, count=1):
    if count<= 0:
        return []
    str = str.lower()
    str = str.rstrip()
    #
    lastWordIndex = str.rfind( ' ', 0, len(str))
    lastWord = ''
    if lastWordIndex == -1:
        return [str]
    else:
        rec = findLastWords(str[:lastWordIndex], count-1)
        rec.append( str[(lastWordIndex+1):] )
        return rec

# Predict the next word using all N-grams starting from the maximal lag
def predictMaxLag(str):
    for gram in Ngrams:
        choice = [ (w,x) for (w,x) in gram.items() if w[:-1] == tuple( str[(len(str)-len(w)+1):] )]
        if choice != []:
            return choice
    return []

import random
def weighted_choice(choice):
   total = sum(w for c, w in choice)
   r = random.uniform(0, total)
   upto = 0
   for c, w in choice:
      if upto + w > r:
         return c
      upto += w
    
    
def generate(str):
    # TODO
    return ""